In [ ]:
!pip install SpeechRecognition pydub

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 32.9/32.9 MB 22.3 MB/s eta 0:00:00


In [ ]:
from IPython.display import HTML, display
import base64
import json
import numpy as np
import soundfile as sf
from google.colab import output

RECORD = """
<button onclick="startRecording()">🎤 Record</button>
<button onclick="stopRecording()">⏹ Stop</button>
<script>
let recorder;
let audioChunks = [];

async function startRecording() {
  const stream = await navigator.mediaDevices.getUserMedia({ audio: true });
  recorder = new MediaRecorder(stream);
  audioChunks = [];
  recorder.ondataavailable = e => audioChunks.push(e.data);
  recorder.start();
}

async function stopRecording() {
  recorder.stop();
  recorder.onstop = async () => {
    const blob = new Blob(audioChunks);
    const buffer = await blob.arrayBuffer();
    const base64data = btoa(
      String.fromCharCode(...new Uint8Array(buffer))
    );
    google.colab.kernel.invokeFunction(
      'notebook.save_audio',
      [base64data],
      {}
    );
  };
}
</script>
"""

display(HTML(RECORD))

In [ ]:
def save_audio(base64data):
    audio_bytes = base64.b64decode(base64data)
    with open("audio.wav", "wb") as f:
        f.write(audio_bytes)

output.register_callback('notebook.save_audio', save_audio)

In [ ]:
import speech_recognition as sr
from pydub import AudioSegment

# Convert the audio file to a standard WAV format
# The MediaRecorder might save in a format that speech_recognition doesn't natively handle
try:
    audio_file_path = "audio.wav"
    sound = AudioSegment.from_file(audio_file_path)
    sound.export(audio_file_path, format="wav")
except Exception as e:
    print(f"Error converting audio file: {e}")

r = sr.Recognizer()
with sr.AudioFile("audio.wav") as source:
    audio = r.record(source)

try:
    text = r.recognize_google(audio, language="id-ID")
    print("Hasil Pengenalan:", text)
except sr.UnknownValueError:
    print("Suara tidak dikenali")
except sr.RequestError as e:
    print(f"Could not request results from Google Speech Recognition service; {e}")
except Exception as e:
    print(f"An unexpected error occurred: {e}")

Hasil Pengenalan: data komputer komputer komputer
